In [1]:
import numpy as np
import pandas as pd

import skimage.io
import skimage.filters
import skimage.morphology

import bokeh.io
from bokeh.layouts import column
from bokeh.io import curdoc, push_notebook, output_notebook

from ipywidgets import interact, interactive, fixed, interact_manual
import ipywidgets as widgets

import bootcamp_utils
import im_click

import segmentation

import traintools

import hypothesis

import matplotlib

import glob

import tqdm

%load_ext line_profiler

bokeh.io.output_notebook()

Loading BokehJS ...

In [37]:
!pytest -v ..

============================= test session starts ==============================
platform darwin -- Python 3.6.5, pytest-3.5.1, py-1.5.3, pluggy-0.6.0 -- /Users/julianwagner/anaconda3/bin/python
cachedir: ../.pytest_cache
rootdir: /Users/julianwagner/git/sceptovideo, inifile:
plugins: remotedata-0.2.1, openfiles-0.3.0, doctestplus-0.1.3, arraydiff-0.2, hypothesis-3.57.0
collected 32 items                                                             

../tests/test_segmentation_pipeline.py::test_im_shape PASSED             [  3%]
../tests/test_segmentation_pipeline.py::test_im_data_type_list PASSED    [  6%]
../tests/test_segmentation_pipeline.py::test_im_data_type_string PASSED  [  9%]
../tests/test_segmentation_pipeline.py::test_im_shape_segment PASSED     [ 12%]
../tests/test_segmentation_pipeline.py::test_im_data_type_list_segment PASSED [ 15%]
../tests/test_segmentation_pipeline.py::test_im_data_type_string_segment PASSED [ 18%]
../tests/test_segmentation_pipeline.py::test_provided_

In [3]:
!ls ../toy_data/

ant_scepto-04092018133745-6089.tiff ant_scepto-04092018133745-6105.tiff
ant_scepto-04092018133745-6090.tiff ant_scepto-04092018133745-6106.tiff
ant_scepto-04092018133745-6091.tiff ant_scepto-04092018133745-6107.tiff
ant_scepto-04092018133745-6092.tiff ant_scepto-04092018133745-6108.tiff
ant_scepto-04092018133745-6093.tiff ant_scepto-04092018133745-6109.tiff
ant_scepto-04092018133745-6094.tiff ant_scepto-04092018133745-6110.tiff
ant_scepto-04092018133745-6095.tiff ant_scepto-04092018133746-6111.tiff
ant_scepto-04092018133745-6096.tiff ant_scepto-04092018133746-6112.tiff
ant_scepto-04092018133745-6097.tiff ant_scepto-04092018133746-6113.tiff
ant_scepto-04092018133745-6098.tiff ant_scepto-04092018133746-6114.tiff
ant_scepto-04092018133745-6099.tiff ant_scepto-04092018133746-6115.tiff
ant_scepto-04092018133745-6100.tiff ant_scepto-04092018133746-6116.tiff
ant_scepto-04092018133745-6101.tiff ant_scepto-04092018133746-6117.tiff
ant_scepto-04092018133745-6102.tiff ant_scepto-04092018133746-61

In [4]:
im_fs = glob.glob('../toy_data/ant_*.tiff')
ims = [skimage.io.imread(x) for x in im_fs]
im_bg = skimage.io.imread('../toy_data/col_filed.tiff')

In [5]:
bokeh.io.show(im_click.im_click(ims[0]))

In [6]:
im_roi = segmentation.give_roi_of_image(ims[0],
                                        cent=((200, 238), (461, 232)),
                                        roi_kind=('ellipse', 'ellipse'),
                                        height=(126, 126),
                                        width=(126, 126))
bokeh.io.show(bootcamp_utils.viz.bokeh_imshow(im_roi))

In [7]:
im_crop = segmentation.crop_image_rectangle(ims[0],
                                        cent=(200, 238),
                                        height=126,
                                        width=126)
bokeh.io.show(bootcamp_utils.viz.bokeh_imshow(im_crop))

In [8]:
im_no_bg = segmentation.bg_subtract(ims[0], im_bg)
im_cropped = segmentation.crop_image_rectangle(im_no_bg,
                                        cent=(200, 238),
                                        height=126,
                                        width=126)
im_bw, _, _ = segmentation.segment(im_cropped, thresh_func=lambda x: skimage.filters.threshold_otsu(x) + 0.15)
bokeh.io.show(bokeh.layouts.column([bootcamp_utils.bokeh_imshow(im_cropped),
                                   bootcamp_utils.bokeh_imshow(im_bw)]))

In [9]:
im_no_bg = segmentation.bg_subtract(ims[0], im_bg)
im_roi = segmentation.give_roi_of_image(im_no_bg,
                                        cent=((200, 238), (461, 232)),
                                        roi_kind=('ellipse', 'ellipse'),
                                        height=(126, 126),
                                        width=(126, 126))
im_bw, _, _ = segmentation.segment(im_roi, thresh_func=0.65)
bokeh.io.show(bokeh.layouts.column([bootcamp_utils.bokeh_imshow(im_roi),
                                   bootcamp_utils.bokeh_imshow(im_bw)]))

In [21]:
plots = []
attributes = []
for im in tqdm.tqdm_notebook(ims):
    im_no_bg = segmentation.bg_subtract(im, im_bg)
    im_roi = segmentation.give_roi_of_image(im_no_bg,
                                            cent=((200, 238), (461, 232)),
                                            roi_kind=('ellipse', 'ellipse'),
                                            height=(126, 126),
                                            width=(126, 126))
    im_bw, im_lab, n_labs = segmentation.segment(im_roi, thresh_func=0.6)
    blobs = skimage.measure.regionprops(skimage.morphology.remove_small_objects(im_lab, min_size=20),
                                        intensity_image=im)
    for blob in blobs:
        atts, labs = segmentation.region_props_to_tuple(blob)
        attributes.append(atts)

In [27]:
pd.DataFrame(attributes, columns=labs).head()

area  bbox_min_row  bbox_min_col  bbox_max_row  bbox_max_col  bbox_area  \
0   330           131           136           171           153     307200   
1  1173           208           167           286           215     307200   
2   304           209           400           241           421     307200   
3  1238           247           378           298           449     307200   
4   292           124           135           155           171     307200   

   centroid_row  centroid_col  convex_area  eccentricity  \
0    150.927273    143.542424          409      0.964992   
1    246.308610    185.986360         2655      0.897012   
2    225.338816    411.279605          381      0.940416   
3    269.903877    409.910339         2165      0.937385   
4    138.380137    148.013699          418      0.970649   

              ...               mean_intensity  min_intensity  \
0             ...                    66.806061             29   
1             ...                    72.627451             17   
2             ...                    64.006579             27   
3             ...                    63.582391             17   
4             ...                    71.082192             27   

   minor_axis_length  orientation   perimeter  solidity  \
0          10.727620     1.265205   99.633514  0.806846   
1          32.064641    -1.473789  386.663997  0.441808   
2          11.799921    -1.048417   94.669048  0.797900   
3          26.556589    -0.333633  342.220346  0.571824   
4          10.333490     0.660565  107.396970  0.698565   

   weighted_centroid_row  weighted_centroid_col  weighted_local_centoid_row  \
0             150.183525             143.805180                   19.183525   
1             248.568187             186.772185                   40.568187   
2             224.167900             410.632542                   15.167900   
3             270.750010             412.974490                   23.750010   
4             137.289169             149.552804                   13.289169   

   weighted_local_centroid_col  
0                     7.805180  
1                    19.772185  
2                    10.632542  
3                    34.974490  
4                    14.552804  

[5 rows x 29 columns]

In [7]:
im_test, _, _ = segmentation.segment(segmentation.bg_subtract(ims[0], im_bg)[131:171, 136:153], 0.6)
bokeh.io.show(bootcamp_utils.viz.bokeh_imshow(im_test))

In [38]:
point_labels = traintools.point_label(ims)

In [8]:
frame_labels = traintools.binary_label(ims, 'beetle', 'ant')

In [22]:
np.array([[(1, 2), [1, 2]], [[1, 2], [1, 2]]]).dtype

dtype('int64')